# <center>pzph1.py guide</center>

### Installation

Create environment with following requrements and put pzph1 directory anywhere you need(or look for `requirements_fullenv.txt` to get full list of packages inn my environment):

In [1]:
%cat /data/SRGz/pzph1/requirements.txt

cat: /data/SRGz/pzph1/requirements.txt: No such file or directory


In [2]:
!python3 /data/SRGz/pzph1/pzph1.py -h

usage: pzph1.py [-h] [--xrayCatalog XRAYCATALOG] [--xrayRaCol XRAYRACOL]
                [--xrayHealpixId XRAYHEALPIXID] [--baseCatalog BASECATALOG]
                [--baseRaCol BASERACOL] [--baseDecCol BASEDECCOL]
                [--xrayDecCol XRAYDECCOL] [--sdss SDSS] [--ps PS] [--ls LS]
                [--sdssOn SDSSON] [--psOn PSON] [--lsOn LSON]
                [--assembledDataset ASSEMBLEDDATASET] [--predictOn PREDICTON]
                [-o OUTPUTDIR] [--primaryRadius PRIMARYRADIUS]
                [--secondaryRadius SECONDARYRADIUS] [--coldStart]
                [--cleanupBuffer] [--modelsSeries MODELSSERIES]
                [--modelsIds MODELSIDS [MODELSIDS ...]] [--useWiseForced]
                [--keepModelsInMemory] [--chunkSize CHUNKSIZE] [--njobs NJOBS]
                [--getaroundrPath GETAROUNDRPATH] [--psFluxesManually]
                [--psFluxesPath PSFLUXESPATH]

Script to make photo-z estimations for eRosita. Note that all arguments are specified as optional because

In [4]:
%cd /data/SRGz/
!mkdir LH_20200514_results_new3
%cd LH_20200514_results_new3

/data/SRGz
/data/SRGz/LH_20200514_results_new3


# Все за один шаг

In [6]:
!nice -20 python3 /data/SRGz/pzph1/pzph1.py --outputDir ./ --baseCatalog ls \
        --xrayCatalog ../LH_20200514/srclist_lockman_032_wvsh.pkl --primaryRadius=30 \
        --xrayRaCol RA --xrayDecCol DEC \
        --baseRaCol ra --baseDecCol dec \
        --njobs 12 --chunkSize 99999 \
        --modelsSeries x1 --modelsIds 18 19 21 22 34 35

Namespace(assembledDataset=None, baseCatalog='ls', baseDecCol='dec', baseRaCol='ra', chunkSize=99999, cleanupBuffer=False, coldStart=False, getaroundrPath='/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py', keepModelsInMemory=False, ls=None, lsOn=None, modelsIds=[18, 19, 21, 22, 34, 35], modelsSeries='x1', njobs=12, outputDir='./', predictOn=None, primaryRadius=30.0, ps=None, psFluxesManually=False, psFluxesPath=None, psOn=None, sdss=None, sdssOn=None, secondaryRadius=1.0, useWiseForced=False, xrayCatalog='../LH_20200514/srclist_lockman_032_wvsh.pkl', xrayDecCol='DEC', xrayHealpixId=None, xrayRaCol='RA')
[('part-00000', 'xray')]
[]
  0%|                                                     | 0/1 [00:00<?, ?it/s]part-00000
('ra', 'dec')
===== Defined use case: 1 =====
===== ====== CORRELATE ====== =====
/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py -i ./buf/__buf__/cross-match_x-ray_coords.fits -r 30.0 -cat decals8tr -o ./buf/__buf__/part-00000.ls_fluxes.fits -asfx _input -iRA

## Шаг 1 - кросс-отождествление и запрос к БД PanSTARRS

In [5]:
# Step1: correlate data and get panstarrs objids list
!nice -20 python3 /data/SRGz/pzph1/pzph1.py --outputDir temp --baseCatalog ls \
        --xrayCatalog ../LH_20200514/srclist_lockman_032_wvsh.pkl --primaryRadius=30 \
        --xrayRaCol RA --xrayDecCol DEC \
        --baseRaCol ra --baseDecCol dec \
        --njobs 24 --chunkSize 99999 \
        --psFluxesManually

Namespace(assembledDataset=None, baseCatalog='ls', baseDecCol='dec', baseRaCol='ra', chunkSize=99999, cleanupBuffer=False, coldStart=False, getaroundrPath='/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py', keepModelsInMemory=False, ls=None, lsOn=None, modelsIds=None, modelsSeries='qso1', njobs=24, outputDir='temp', predictOn=None, primaryRadius=30.0, ps=None, psFluxesManually=True, psFluxesPath=None, psOn=None, sdss=None, sdssOn=None, secondaryRadius=1.0, useWiseForced=False, xrayCatalog='../LH_20200514/srclist_lockman_032_wvsh.pkl', xrayDecCol='DEC', xrayHealpixId=None, xrayRaCol='RA')
Preparing data: 100%|█████████████████████████████| 1/1 [00:00<00:00,  7.26it/s]
[('part-00000', 'xray')]
[]
  0%|                                                     | 0/1 [00:00<?, ?it/s]part-00000
('ra', 'dec')
===== Defined use case: 1 =====
===== ====== CORRELATE ====== =====
/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py -i temp/buf/__buf__/cross-match_x-ray_coords.fits -r 30.0 -cat dec

рассмотрим запуск подробнее:

- `--outputDir` указывает путь к целевой директории. Если она не существет, то скрип её создаст
- `--baseCatalog` - базовый оптический каталог. Пока доступен только ls (DESI LIS). Иначе будет `AssertionError`
- `--xrayCatalog` указывает путь до рентгеновского каталога (fits, pkl или gz_pkl)
- `--primaryRadius` в каком радиусе искать оптических компаньонов в базовом оптическом каталоге
- `--secondaryRadius` радиус для отождествления оптических компаньонов с другими каталогами (в данном случае PS и LS). По умолчанию равен 1 секунде
- `--xrayRaCol`, `--xrayDecCol` - названия столбцов с координатами в `--xrayCatalog`
- `--baseRaCol`, `--baseDecCol` - названия столбцов с координатами в базовом каталоге
- `--njobs`
- `--chunkSize` - размер куска данных в смысле рентгеновских объектов. Чтобы использовать разбиение, заданное значениями некоторого столбца в `--xrayCatalog`, нужно в параметре `--xrayHealpixId` указать название этого столбца. Тогда `--chunkSize` игнорируется
- `--psFluxesManually` - флаг, который указывает, что потоки PanSTARRS будут получены вручную из casjobs. Чтобы использовать ps2olldflux, нужно не указывать этот флаг.
- Модели применяться не будут, поскольку не указан `--modelsIds`

#### Посмотрим, что получилось

Выходную директорию указывали `--output results/ps`
В ней находится директории с данными, разбитыми на куски, промежуточными результатами и `ps_objids.csv`, который нужен для запроса к БД PanSTARRS

In [6]:
!ls -lh temp/

total 4.3M
drwxrwxr-x. 3 victor victor   29 Oct 28 18:28 buf
drwxrwxr-x. 2 victor victor   77 Oct 28 18:28 data
-rw-rw-r--. 1 victor victor 4.3M Oct 28 18:42 ps_objids.csv


в директории `data` содержится датасет, разбитый на куски и `DATA_WRITTEN_FILE.txt`, означающий, что данные разбиты и записаны успешно. При повторном запуске скрипт будет пытаться его найти, и, если найдет, то не будет читать оригинальные данные заново. Иначе, он разобъет и запишет заново

In [7]:
!ls -lh temp/data

total 696K
-rw-rw-r--. 1 victor victor    0 Oct 28 18:28 DATA_WRITTEN_FILE.txt
-rw-rw-r--. 1 victor victor 693K Oct 28 18:28 part-00000.xray.gz_pkl


в директории `buf` находится пока только директория с результатми кросс-отождествления

In [8]:
!ls -lh temp/buf/

total 4.0K
drwxrwxr-x. 2 victor victor 4.0K Oct 28 18:42 __buf__


в ней можно найти сами результаты и std-outы и std-errы коррелятора Георгия, чтобы можно было узнать причину падения на этапе корреляции

In [9]:
!ls -lh temp/buf/__buf__ | head -20

total 248M
-rw-rw-r--. 1 victor victor 2.9M Oct 28 18:29 cross-match_base_catalog_coords.fits
-rw-rw-r--. 1 victor victor 206K Oct 28 18:28 cross-match_x-ray_coords.fits
-rw-rw-r--. 1 victor victor 173M Oct 28 18:29 part-00000.ls_fluxes.fits
-rw-rw-r--. 1 victor victor    0 Oct 28 18:28 part-00000.ls_fluxes.stderr.20201028152809.txt
-rw-rw-r--. 1 victor victor  34K Oct 28 18:29 part-00000.ls_fluxes.stdout.20201028152809.txt
-rw-rw-r--. 1 victor victor  42M Oct 28 18:42 part-00000.ps_fluxes.fits
-rw-rw-r--. 1 victor victor    0 Oct 28 18:39 part-00000.ps_fluxes.stderr.20201028153927.txt
-rw-rw-r--. 1 victor victor 2.4K Oct 28 18:42 part-00000.ps_fluxes.stdout.20201028153927.txt
-rw-rw-r--. 1 victor victor  27M Oct 28 18:39 part-00000.sdss_fluxes.fits
-rw-rw-r--. 1 victor victor    0 Oct 28 18:29 part-00000.sdss_fluxes.stderr.20201028152943.txt
-rw-rw-r--. 1 victor victor  66K Oct 28 18:39 part-00000.sdss_fluxes.stdout.20201028152943.txt


В запросе к Casjobs помимо предлагаемых скриптом столбцов, можно запрашивать и другие. Если эти другие столбцы есть в корреляторе, то скрипт даст предпочтение данным из casjobs и заменит значения коррелятора в этих столбцах на значения из casjpbs

In [10]:
# helper step: objids to upload
!cp temp/ps_objids.csv ~/

In [11]:
# helper step: copy panstarrs fluxes obtained from casjobs
!mv /home/victor/lh_ls_res_tibercus.csv temp/ -v

'/home/victor/lh_ls_res_tibercus.csv' -> 'temp/lh_ls_res_tibercus.csv'
removed '/home/victor/lh_ls_res_tibercus.csv'


## Шаг 2 - объединение данных каталогов

In [5]:
# Step2: merge all data
!nice -20 python3 /home/victor/pzphlib/pzph1.py --outputDir temp --baseCatalog ls \
        --xrayCatalog ../LH_20200514/srclist_lockman_032_wvsh.pkl --primaryRadius=30 \
        --xrayRaCol RA --xrayDecCol DEC \
        --baseRaCol ra --baseDecCol dec \
        --njobs 24 --chunkSize 99999 \
        --psFluxesManually --psFluxesPath temp/lh_ls_res_tibercus.csv

Namespace(assembledDataset=None, baseCatalog='ls', baseDecCol='dec', baseRaCol='ra', chunkSize=99999, cleanupBuffer=False, coldStart=False, getaroundrPath='/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py', keepModelsInMemory=False, ls=None, lsOn=None, modelsIds=None, modelsSeries='qso1', njobs=24, outputDir='temp', predictOn=None, primaryRadius=30.0, ps=None, psFluxesManually=True, psFluxesPath='temp/lh_ls_res_tibercus.csv', psOn=None, sdss=None, sdssOn=None, secondaryRadius=1.0, useWiseForced=False, xrayCatalog='../LH_20200514/srclist_lockman_032_wvsh.pkl', xrayDecCol='DEC', xrayHealpixId=None, xrayRaCol='RA')
[('part-00000', 'xray')]
[]
  0%|                                                     | 0/1 [00:00<?, ?it/s]part-00000
('ra', 'dec')
===== Defined use case: 1 =====
===== Correlate with sdss =====
===== Done =====
===== Correlate with ps =====
===== Done =====
/home/victor/pzphlib/pzph1.py:814: UserWarning: multidimentional columns are dropped from table : ['PSFFLUX', 'PSFF

На данном этапе дополнительно указываем путь к потокам, полученным из casjobs в параметр `--psFluxesPath`

#### Посмотрим, что получилось

Здесь добавился только файл с потоками из БД PS, который мы положили ранее

In [6]:
!ls temp/

buf  data  lh_ls_res_tibercus.csv  ps_objids.csv


В директории `buf` теперь будут файлы `features`, которые содержат дданные SDSS, PS и DESI LIS и признаки, посчитанные без разыгрываний и учета ошибок. Признаки носят исключительно информативный характер, так скажем, потому что для разных моделей нужны признаки с/без поглощением и т.д. На этапе применения они подсчитываются заново и никуда не записываются.

Файлы `features` можно [часть из них, или все] переместить в другую директорию/на другую машину и запустить применение моделей, как показано ниже. В таком сценарии нужно НЕ указывать параметр `--modelsIds`. Тогда модели не будут применены

In [7]:
!ls temp/buf

__buf__  part-00000.features.gz_pkl


## Шаг 3 - прогноз и постобработка файлов

Смоделируем ситуацию, что файлы с фичами были перенесены на другую машину

In [8]:
!ls temp/buf

__buf__  part-00000.features.gz_pkl


In [9]:
!mkdir features_files
!cp temp/buf/*.features.gz_pkl features_files/ -v

'temp/buf/part-00000.features.gz_pkl' -> 'features_files/part-00000.features.gz_pkl'


Чтобы скрипту подать на вход файлы `features`, необходимо указать в параметре `--predictOn` директорию, где они лежат. Скрипт будет их искать в этой директории, скопирует в целевую директорию `--outputDir` и применит модели.

In [10]:
# Step3: predict
!nice -20 python3 /home/victor/pzphlib/pzph1.py --outputDir predictions_files \
        --baseCatalog ls \
        --predictOn features_files \
        --njobs 24 --modelsSeries x1 --modelsIds 18 19 21 22 34 35

Namespace(assembledDataset=None, baseCatalog='ls', baseDecCol='dec', baseRaCol='ra', chunkSize=100000, cleanupBuffer=False, coldStart=False, getaroundrPath='/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py', keepModelsInMemory=False, ls=None, lsOn=None, modelsIds=[18, 19, 21, 22, 34, 35], modelsSeries='x1', njobs=24, outputDir='predictions_files', predictOn='features_files', primaryRadius=30.0, ps=None, psFluxesManually=False, psFluxesPath=None, psOn=None, sdss=None, sdssOn=None, secondaryRadius=1.0, useWiseForced=False, xrayCatalog=None, xrayDecCol='DEC_', xrayHealpixId=None, xrayRaCol='RA_')
Perturbations: 100%|███████████████████▉| 122426/122447 [07:50<00:00, 65.48it/s]
                                                                                /home/victor/pzphlib/pzph1.py:1210: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pand

рассмотрим запуск подробнее:

- `--outputDir`
- `--predictOn` - директория с файлами features
- `--njobs`
- `--modelsSeries` - модели какой линейки применить. Чтобы применить модели нескольких линеек, стоит запускать скрипт повторно с необходимыми `--modelsSeries` и `--modelsIds`
- `--modelsIds` - номера моделей, которые нужно применить. Список доступных моделей см. в `--help`

#### Посмотрим, что получили

В директории `buf` находятся файлы вида `fearures`, полученные на этапе предобработки и/или поданные через параметр `--predictOn` и файлы вида `part-00000.pdfs.<model_id>.gz_pkl` и `part-00000.preds.<model_id>.gz_pkl`

Первые содержат полный ансамбль прогноза отдельно для каждой модели. Вторые - производные полного прогноза - z_max, zConf и т.д. отдельно для каждой модели. Для удобства эти файлы собираются в единый файл `part-00000.predictions.<model_series>.gz_pkl`, а так же по заранее составленному рейтингу моделей выбирается прогноз лучшей возможной модели для каждого объекта и записываются в `part-00000.best.<model_series>.gz_pkl`

In [11]:
!ls predictions_files

buf			   part-00000.features.gz_pkl
part-00000.best.x1.gz_pkl  part-00000.predictions.x1.gz_pkl


In [12]:
!ls predictions_files/buf | head -20

part-00000.features.gz_pkl
part-00000.pdfs.x118.gz_pkl
part-00000.pdfs.x119.gz_pkl
part-00000.pdfs.x121.gz_pkl
part-00000.pdfs.x122.gz_pkl
part-00000.pdfs.x134.gz_pkl
part-00000.pdfs.x135.gz_pkl
part-00000.preds.x118.gz_pkl
part-00000.preds.x119.gz_pkl
part-00000.preds.x121.gz_pkl
part-00000.preds.x122.gz_pkl
part-00000.preds.x134.gz_pkl
part-00000.preds.x135.gz_pkl


# Шаг 4 - как работать с прогнозами?

In [13]:
import pandas as pd
pd.set_option('display.max_rows', 100, 'display.max_columns', None, 'display.max_colwidth', 100)

In [14]:
data = pd.concat([
    pd.concat([
        pd.read_pickle(f'/data/SRGz/LH_20200514_results_new/predictions_files/part-{i:05d}.features.gz_pkl',
                       compression='gzip'),
        pd.read_pickle(f'/data/SRGz/LH_20200514_results_new/predictions_files/part-{i:05d}.predictions.x1.gz_pkl',
                       compression='gzip'),
        pd.read_pickle(f'/data/SRGz/LH_20200514_results_new/predictions_files/part-{i:05d}.best.x1.gz_pkl',
                       compression='gzip'),
    ], axis=1)  # DO NOT FORGET AXIS=1 WHEN JOINING FEATURES, PREDICTIONS AND BEST FILES
                # FOR SINGLE PART
    for i in range(1)
])

In [15]:
data['ps_objID'].dtype

dtype('O')

Рассмотрим подробнее, что имеем

Сначала идут рентгеновские атрибуты. Имена столбцов у них не изменяются

In [31]:
from pprint import pprint

In [32]:
pprint(list(data.columns[:27]), compact=True)

['ID_SRC', 'RA', 'DEC', 'RADEC_ERR', 'EXT', 'DET_LIKE_0', 'ML_FLUX_0',
 'ML_FLUX_ERR_0', 'EXT_LIKE', 'EXT_ERR', 'ID_CLUSTER', 'DIST_NN', 'ML_CTS_0',
 'ML_CTS_ERR_0', 'ML_BKG_0', 'SRCDENS', 'TSTART', 'TSTOP', 'ML_EXP_1',
 'APE_CTS_1', 'APE_BKG_1', 'APE_EXP_1', 'APE_EEF_1', 'APE_RADIUS_1',
 'APE_POIS_1', 'RA_corr', 'DEC_corr']


Затем идет "рабочий" ID объекта. Он локален для каждого part-а

In [33]:
pprint(list(data.columns[27:28]))

['__workxid__']


Затем идут атрибуты DESI LIS. У названий столбцов добавлен префикс "ls_". В конце идет рабочий ID оптического компаньона, так же локальный для каждого part-а. Поскольку в нашем случае базовым каталогом является DESI LIS, к названию столбца так же добавлен соответствующий префикс

In [36]:
pprint(list(data.columns[28:167]), compact=True)

['ls_release', 'ls_brickid', 'ls_brickname', 'ls_objid', 'ls_brick_primary',
 'ls_brightblob', 'ls_maskbits', 'ls_type', 'ls_ra', 'ls_dec', 'ls_ra_ivar',
 'ls_dec_ivar', 'ls_bx', 'ls_by', 'ls_ebv', 'ls_mjd_min', 'ls_mjd_max',
 'ls_ref_cat', 'ls_ref_id', 'ls_pmra', 'ls_pmdec', 'ls_parallax',
 'ls_pmra_ivar', 'ls_pmdec_ivar', 'ls_parallax_ivar', 'ls_ref_epoch',
 'ls_gaia_pointsource', 'ls_gaia_phot_g_mean_mag',
 'ls_gaia_phot_g_mean_flux_over_error', 'ls_gaia_phot_g_n_obs',
 'ls_gaia_phot_bp_mean_mag', 'ls_gaia_phot_bp_mean_flux_over_error',
 'ls_gaia_phot_bp_n_obs', 'ls_gaia_phot_rp_mean_mag',
 'ls_gaia_phot_rp_mean_flux_over_error', 'ls_gaia_phot_rp_n_obs',
 'ls_gaia_phot_variable_flag', 'ls_gaia_astrometric_excess_noise',
 'ls_gaia_astrometric_excess_noise_sig', 'ls_gaia_astrometric_n_obs_al',
 'ls_gaia_astrometric_n_good_obs_al', 'ls_gaia_astrometric_weight_al',
 'ls_gaia_duplicated_source', 'ls_gaia_a_g_val', 'ls_gaia_e_bp_min_rp_val',
 'ls_gaia_phot_bp_rp_excess_factor', 'ls_gaia_a

Далее идут атрибуты оставшихся оптических каталогов с соответствующими префиксами в названиях столбцов. Для каждого каталога так же дается служебная информация по обработке дубликатов

In [40]:
pprint(list(data.columns[167:289]), compact=True)

['sdss_objID', 'sdss_MODE', 'sdss_CLEAN', 'sdss_ra', 'sdss_dec', 'sdss_RAERR',
 'sdss_DECERR', 'sdss_cModelFluxIvar_u', 'sdss_cModelFlux_u',
 'sdss_cModelFluxIvar_g', 'sdss_cModelFlux_g', 'sdss_cModelFluxIvar_r',
 'sdss_cModelFlux_r', 'sdss_cModelFluxIvar_i', 'sdss_cModelFlux_i',
 'sdss_cModelFluxIvar_z', 'sdss_cModelFlux_z', 'sdss_psfFluxIvar_u',
 'sdss_psfFlux_u', 'sdss_psfFluxIvar_g', 'sdss_psfFlux_g', 'sdss_psfFluxIvar_r',
 'sdss_psfFlux_r', 'sdss_psfFluxIvar_i', 'sdss_psfFlux_i', 'sdss_psfFluxIvar_z',
 'sdss_psfFlux_z', 'sdss_counterparts_number', 'sdss_single_counterpart',
 'sdss_counterparts_type', 'ps_objID', 'ps_raStack', 'ps_decStack',
 'ps_raStackErr', 'ps_decStackErr', 'ps_raMean', 'ps_decMean', 'ps_raMeanErr',
 'ps_decMeanErr', 'ps_objInfoFlag', 'ps_qualityFlag', 'ps_primaryDetection',
 'ps_bestDetection', 'ps_gPSFMag', 'ps_gPSFMagErr', 'ps_gApMag', 'ps_gApMagErr',
 'ps_gKronMag', 'ps_gKronMagErr', 'ps_rPSFMag', 'ps_rPSFMagErr', 'ps_rApMag',
 'ps_rApMagErr', 'ps_rKronMag',

Далее признаки

In [45]:
pprint(list(data.columns[290:389]), compact=True)

['sdssdr16_g_psf', 'sdssdr16_r_psf', 'sdssdr16_i_psf', 'sdssdr16_z_psf',
 'sdssdr16_u_cmodel', 'sdssdr16_g_cmodel', 'sdssdr16_r_cmodel',
 'sdssdr16_i_cmodel', 'sdssdr16_z_cmodel', 'psdr2_g_kron', 'psdr2_r_kron',
 'psdr2_i_kron', 'psdr2_z_kron', 'psdr2_y_kron', 'psdr2_g_psf', 'psdr2_r_psf',
 'psdr2_i_psf', 'psdr2_z_psf', 'psdr2_y_psf', 'ls_flux_g_ebv', 'ls_flux_r_ebv',
 'ls_flux_z_ebv', 'ls_flux_w1_ebv', 'ls_flux_w2_ebv', 'ls_flux_w3_ebv',
 'ls_flux_w4_ebv', 'decals8tr_g', 'decals8tr_r', 'decals8tr_z', 'decals8tr_Lw1',
 'decals8tr_Lw2', 'decals8tr_Lw3', 'decals8tr_Lw4', 'sdssdr16_u-g_psf',
 'sdssdr16_u-r_psf', 'sdssdr16_u-i_psf', 'sdssdr16_u-z_psf',
 'sdssdr16_u_psf-cmodel', 'sdssdr16_g-r_psf', 'sdssdr16_g-i_psf',
 'sdssdr16_g-z_psf', 'sdssdr16_g_psf-cmodel', 'sdssdr16_r-i_psf',
 'sdssdr16_r-z_psf', 'sdssdr16_r_psf-cmodel', 'sdssdr16_i-z_psf',
 'sdssdr16_i_psf-cmodel', 'sdssdr16_z_psf-cmodel', 'psdr2_g-r_psf',
 'psdr2_g-i_psf', 'psdr2_g-z_psf', 'psdr2_g-y_psf', 'psdr2_g_psf-kron',
 'psd

Далее идут флаги и глобальный ID компаньона `nrow` (счет начинается с 1)

In [48]:
pprint(list(data.columns[390:403]), compact=True)

['phot_is_train_pmatch', 'phot_is_train_pclass', 'phot_is_train_star',
 'phot_is_train_gal', 'phot_is_test_xxln_m16', 'phot_is_test_s82x_l19',
 'phot_is_test_s82x_a17', 'phot_is_test_qso', 'phot_is_test_star',
 'phot_is_test_gal', 'phot_is_spec_sdss', 'phot_test_field', 'nrow']


Прогнозы всех выбранных моделей

In [55]:
pprint(list(data.columns[404:463]), compact=True)

['zoo_x118_z_max', 'zoo_x118_z_maxConf', 'zoo_x118_ci1a_68', 'zoo_x118_ci1b_68',
 'zoo_x118_ci1a_90', 'zoo_x118_ci1b_90', 'zoo_x118_ci1a_95', 'zoo_x118_ci1b_95',
 'ProcessPredictionsError', 'zoo_x119_z_pdf', 'zoo_x119_z_max',
 'zoo_x119_z_maxConf', 'zoo_x119_ci1a_68', 'zoo_x119_ci1b_68',
 'zoo_x119_ci1a_90', 'zoo_x119_ci1b_90', 'zoo_x119_ci1a_95', 'zoo_x119_ci1b_95',
 'ProcessPredictionsError', 'zoo_x121_z_pdf', 'zoo_x121_z_max',
 'zoo_x121_z_maxConf', 'zoo_x121_ci1a_68', 'zoo_x121_ci1b_68',
 'zoo_x121_ci1a_90', 'zoo_x121_ci1b_90', 'zoo_x121_ci1a_95', 'zoo_x121_ci1b_95',
 'ProcessPredictionsError', 'zoo_x122_z_pdf', 'zoo_x122_z_max',
 'zoo_x122_z_maxConf', 'zoo_x122_ci1a_68', 'zoo_x122_ci1b_68',
 'zoo_x122_ci1a_90', 'zoo_x122_ci1b_90', 'zoo_x122_ci1a_95', 'zoo_x122_ci1b_95',
 'ProcessPredictionsError', 'zoo_x134_z_pdf', 'zoo_x134_z_max',
 'zoo_x134_z_maxConf', 'zoo_x134_ci1a_68', 'zoo_x134_ci1b_68',
 'zoo_x134_ci1a_90', 'zoo_x134_ci1b_90', 'zoo_x134_ci1a_95', 'zoo_x134_ci1b_95',
 'Proc

И лучшие прогнозы. В `model_id` указывается, прогноз какой модели был выбран

In [56]:
pprint(list(data.columns[464:]), compact=True)

['zoo_best_z_max', 'zoo_best_z_maxConf', 'zoo_best_ci1a_68', 'zoo_best_ci1b_68',
 'zoo_best_ci1a_90', 'zoo_best_ci1b_90', 'zoo_best_ci1a_95', 'zoo_best_ci1b_95',
 'model_id']


# Пример: прогноз всеми рентгеновскими моделями - старыми и новыми

На данный момент доступно 3 серии моделей:

- x0 - старые модели для рентгеновских объектов. Без учета поглощений и фотометрических ошибок
- x1 - новые модели для рентоеновских объекто. С учетом поглощений и фотометрических ошибок
- gal - модели для оптических галактик. Без учета поглощений и ошибок фотометрических имзерений

Для примера попробуем сделать прогноз всеми рентгеновскими моделями. Для этого нужно запустить скрипт несколько раз, указывая нужные параметры --modelSeries и --modelIds, а остальные параметры фиксировать

In [3]:
# Preprocess data and make prediction with x1-models
!python3 /home/victor/pzphlib/pzph1.py --output example_results --baseCatalog "ls" \
    --xrayCatalog qso2moar/coords.fits --primaryRadius=1 --xrayRaCol ra --xrayDecCol dec \
    --njobs 1 --modelsSeries x1 --modelsIds 18 19 20 21 22 34 35

# Checks that data is preprocessed and maked predictions with x0-models
# change only --modelsSeries and --modelsIds
!python3 /home/victor/pzphlib/pzph1.py --output example_results --baseCatalog "ls" \
    --xrayCatalog qso2moar/coords.fits --primaryRadius=1 --xrayRaCol ra --xrayDecCol dec \
    --njobs 1 --modelsSeries x0 --modelsIds 19 21 22 35

===== Not found PZPH1_FLAGS_DATA_PATH env variable. Using default path: /data/SRGz/pzph1/objids =====
Namespace(assembledDataset=None, baseCatalog='ls', baseDecCol='dec', baseRaCol='ra', chunkSize=100000, cleanupBuffer=False, coldStart=False, getaroundrPath='/home/horungev/Catalogs/SRG/crossmatch/getaroundr.py', keepModelsInMemory=False, ls=None, lsOn=None, modelsIds=[18, 19, 20, 21, 22, 34, 35], modelsSeries='x1', njobs=1, outputDir='example_results', predictOn=None, primaryRadius=1.0, ps=None, psFluxesManually=False, psFluxesPath=None, psOn=None, sdss=None, sdssOn=None, secondaryRadius=1.0, useWiseForced=False, xrayCatalog='qso2moar/coords.fits', xrayDecCol='dec', xrayHealpixId=None, xrayRaCol='ra')
Preparing data: 100%|████████████████████████████| 1/1 [00:00<00:00, 677.05it/s]
[('part-00000', 'xray')]
[]
  0%|                                                     | 0/1 [00:00<?, ?it/s]part-00000
('ra', 'dec')
===== Defined use case: 1 =====
===== ====== CORRELATE ====== =====
/home/h

In [14]:
# lets see results
import glob
import IPython.display as ipd
import pandas as pd

features = pd.read_pickle('example_results/part-00000.features.gz_pkl', compression='gzip')
preds_x0 = pd.read_pickle('example_results/part-00000.predictions.x0.gz_pkl', compression='gzip')
preds_x1 = pd.read_pickle('example_results/part-00000.predictions.x1.gz_pkl', compression='gzip')

results = pd.concat([features, preds_x0, preds_x1], axis=1)

ipd.display(results[['objName', 'zoo_x035_z_max', 'zoo_x035_z_maxConf', 'zoo_x135_z_max', 'zoo_x135_z_maxConf']])
list(results)[346:]

objName zoo_x035_z_max zoo_x035_z_maxConf zoo_x135_z_max  \
0  b'SRGe J020142.9-015348'              5                  1        5.02008   
1  b'SRGe J234248.8+303712'        2.06981           0.284437           5.03   

  zoo_x135_z_maxConf  
0                  1  
1           0.591113

['zoo_x019_z_pdf',
 'zoo_x019_z_max',
 'zoo_x019_z_max_proba',
 'zoo_x019_z_maxConf',
 'zoo_x019_proba_z_ge_3',
 'zoo_x019_ci1_68',
 'zoo_x019_ci2_68_short',
 'zoo_x019_ci2_68',
 'zoo_x019_ci2_68_peaks',
 'zoo_x019_ci2_68_peaks_proba',
 'zoo_x019_ci2_68_peaks_zConf',
 'zoo_x019_ci1_90',
 'zoo_x019_ci2_90_short',
 'zoo_x019_ci2_90',
 'zoo_x019_ci2_90_peaks',
 'zoo_x019_ci2_90_peaks_proba',
 'zoo_x019_ci2_90_peaks_zConf',
 'zoo_x019_ci1_95',
 'zoo_x019_ci2_95_short',
 'zoo_x019_ci2_95',
 'zoo_x019_ci2_95_peaks',
 'zoo_x019_ci2_95_peaks_proba',
 'zoo_x019_ci2_95_peaks_zConf',
 'zoo_x019_mean',
 'zoo_x019_std',
 'zoo_x019_skewness',
 'zoo_x019_kurtosis',
 'zoo_x019_entropy',
 'zoo_x019_ProcessPredictionsError',
 'zoo_x021_z_pdf',
 'zoo_x021_z_max',
 'zoo_x021_z_max_proba',
 'zoo_x021_z_maxConf',
 'zoo_x021_proba_z_ge_3',
 'zoo_x021_ci1_68',
 'zoo_x021_ci2_68_short',
 'zoo_x021_ci2_68',
 'zoo_x021_ci2_68_peaks',
 'zoo_x021_ci2_68_peaks_proba',
 'zoo_x021_ci2_68_peaks_zConf',
 'zoo_x021_ci1_